# Gets list of candidate reactions for overexpression
## Written by: Wheaton Schroeder
### Latest version: 08/30/2023

#### make necessary imports

In [1]:
import pandas as pd
import cobra
import re
import shutil

#### Set run parameters

In [2]:
harvest = "H2"
drought_file = "./iPotri2999D.xml"

#### read in the FVA results

In [3]:
#read in the drought FVA result
drought_df = pd.read_table('./GAMS/FVA_result_'+harvest+'.txt')

#get list of reactions in the drought
drought_rxn_list = drought_df.rxn.to_list()

#clean up by removing the unnecessary spaces
for rxn in drought_rxn_list:

  #cleaned reaction
  cleaned_rxn = rxn.replace(" ","")

  drought_df.loc[drought_rxn_list.index(rxn),'rxn'] = cleaned_rxn
  drought_rxn_list[drought_rxn_list.index(rxn)] = cleaned_rxn

#set the reaction as the index
drought_df = drought_df.set_index('rxn')

#for debugging
drought_df

LB       min         max  \
rxn                                                                           
RXN_UDPREDUCT_RXN_p__L___LIGHT               -10000.0  0.000000    0.000000   
RXN_E2C_mg2__L___LIGHT                       -10000.0  0.000000    0.000000   
RXN_ICOSANOYL_COA_SYNTHASE_RXN_er__L___LIGHT -10000.0  0.000000    0.000000   
RXN_GPH_RXN_er__L___LIGHT                         0.0  0.000000   12.369937   
RXN_RXN_15816__L___LIGHT                     -10000.0  0.000000  128.602453   
...                                               ...       ...         ...   
SK_MET_carbon_dioxide_c__S___LIGHT            -1000.0 -0.920916   -0.920892   
DM_MET_starch_p__L___LIGHT                        0.0  0.561231    0.561282   
DM_MET_starch_p__S___LIGHT                        0.0  0.282929    0.282962   
SK_MET_starch_p__L___DARK                     -1000.0 -0.561282   -0.561231   
SK_MET_starch_p__S___DARK                     -1000.0 -0.282962   -0.282929   

                                                   UB  ModelStat  SolveStat  
rxn                                                                          
RXN_UDPREDUCT_RXN_p__L___LIGHT                    0.0        1.0        1.0  
RXN_E2C_mg2__L___LIGHT                        10000.0        1.0        1.0  
RXN_ICOSANOYL_COA_SYNTHASE_RXN_er__L___LIGHT  10000.0        1.0        1.0  
RXN_GPH_RXN_er__L___LIGHT                     10000.0        1.0        1.0  
RXN_RXN_15816__L___LIGHT                      10000.0        1.0        1.0  
...                                               ...        ...        ...  
SK_MET_carbon_dioxide_c__S___LIGHT                0.0        1.0        1.0  
DM_MET_starch_p__L___LIGHT                     1000.0        1.0        1.0  
DM_MET_starch_p__S___LIGHT                     1000.0        1.0        1.0  
SK_MET_starch_p__L___DARK                         0.0        1.0        1.0  
SK_MET_starch_p__S___DARK                         0.0        1.0        1.0  

[10036 rows x 6 columns]

In [4]:
cont_df = pd.read_table('./GAMS/FVA_result_C.txt')

#get list of reactions in the control
cont_rxn_list = cont_df.rxn.to_list()

#clean up by removing the unnecessary spaces
for rxn in cont_rxn_list:

  #cleaned reaction
  cleaned_rxn = rxn.replace(" ","")

  cont_df.loc[cont_rxn_list.index(rxn),'rxn'] = cleaned_rxn
  cont_rxn_list[cont_rxn_list.index(rxn)] = cleaned_rxn

#set the reaction as the index
cont_df = cont_df.set_index('rxn')

#for debugging
cont_df

LB       min         max  \
rxn                                                                           
RXN_UDPREDUCT_RXN_p__L___LIGHT               -10000.0  0.000000    0.000000   
RXN_E2C_mg2__L___LIGHT                       -10000.0  0.000000    0.000000   
RXN_RXN_11755_er__L___LIGHT                       0.0  0.000000  178.893509   
RXN_ICOSANOYL_COA_SYNTHASE_RXN_er__L___LIGHT -10000.0  0.000000    0.000000   
RXN_GPH_RXN_er__L___LIGHT                         0.0  0.000000   18.181554   
...                                               ...       ...         ...   
SK_MET_carbon_dioxide_c__S___LIGHT            -1000.0 -1.141754   -1.141753   
DM_MET_starch_p__L___LIGHT                        0.0  0.703488    0.703488   
DM_MET_starch_p__S___LIGHT                        0.0  0.354921    0.354921   
SK_MET_starch_p__L___DARK                     -1000.0 -0.703488   -0.703488   
SK_MET_starch_p__S___DARK                     -1000.0 -0.354921   -0.354921   

                                                   UB  ModelStat  SolveStat  
rxn                                                                          
RXN_UDPREDUCT_RXN_p__L___LIGHT                    0.0        1.0        1.0  
RXN_E2C_mg2__L___LIGHT                        10000.0        1.0        1.0  
RXN_RXN_11755_er__L___LIGHT                   10000.0        1.0        1.0  
RXN_ICOSANOYL_COA_SYNTHASE_RXN_er__L___LIGHT  10000.0        1.0        1.0  
RXN_GPH_RXN_er__L___LIGHT                     10000.0        1.0        1.0  
...                                               ...        ...        ...  
SK_MET_carbon_dioxide_c__S___LIGHT                0.0        1.0        1.0  
DM_MET_starch_p__L___LIGHT                     1000.0        1.0        1.0  
DM_MET_starch_p__S___LIGHT                     1000.0        1.0        1.0  
SK_MET_starch_p__L___DARK                         0.0        1.0        1.0  
SK_MET_starch_p__S___DARK                         0.0        1.0        1.0  

[9726 rows x 6 columns]

#### Read in reactions that are downregulated in the leaf

##### leaf

In [5]:
#read the list of genes downregulated in the leaf
down_leaf_f = open("./DGE_analysis/downRegulated_LEAF.txt")

#initialize a list for them
down_leaf = list()

#read the file into the list
for gene in down_leaf_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  down_leaf.append(gene_temp)

##### root

In [6]:
#read the list of genes downregulated in the root
down_root_f = open("./DGE_analysis/downRegulated_ROOT.txt")

#initialize a list for them
down_root = list()

#read the file into the list
for gene in down_root_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  down_root.append(gene_temp)

##### stem

In [7]:
#read the list of genes downregulated in the root
down_stem_f = open("./DGE_analysis/downRegulated_STEM.txt")

#initialize a list for them
down_stem = list()

#read the file into the list
for gene in down_stem_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  down_stem.append(gene_temp)

#### Read in upregulated gene sets

##### Leaf

In [8]:
#read the list of genes downregulated in the leaf
up_leaf_f = open("./DGE_analysis/upregulated_LEAF.txt")

#initialize a list for them
up_leaf = list()

#read the file into the list
for gene in up_leaf_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  up_leaf.append(gene_temp)

##### Root

In [9]:
#read the list of genes downregulated in the root
up_root_f = open("./DGE_analysis/upregulated_ROOT.txt")

#initialize a list for them
up_root = list()

#read the file into the list
for gene in up_root_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  up_root.append(gene_temp)

##### Stem

In [10]:
#read the list of genes downregulated in the root
up_stem_f = open("./DGE_analysis/upregulated_STEM.txt")

#initialize a list for them
up_stem = list()

#read the file into the list
for gene in up_stem_f:

  #remove newline characters
  gene_temp = gene.replace("\n","")

  #remove unnecessary spaces
  gene_temp = gene_temp.replace(" ","")
  
  #add to the 
  up_stem.append(gene_temp)

#### Read in the drought model for GPR

In [11]:
drought_model = cobra.io.read_sbml_model(drought_file)

print("success")

No objective coefficients in model. Unclear what should be optimized


success


#### identify candidates, report on results simultaneously

In [12]:
#open file to write candidates to
kd_cand_f = open("./kd_results/kd_candidates_"+harvest+".txt","w")

kd_cand_f.write("/")

#since we only want reactions in drought and control, iterating over a single one is OK
for rxn in cont_rxn_list:
    
    #check if in drought, do nothing it it is not
    if rxn in drought_rxn_list:

      print("\nanalyzing reaction ",rxn)
        
      #at this point, we know the reaction is in both drought and control
      #get min and max values in control and drought
      fva_min_d = drought_df.loc[rxn,'min']
      fva_max_d = drought_df.loc[rxn,'max']
      fva_min_c = cont_df.loc[rxn,'min']
      fva_max_c = cont_df.loc[rxn,'max']

      print("min_d: ",str(fva_min_d),"\tmax_d: ",str(fva_max_d),"min_c: ",str(fva_min_c),"\tmax_c: ",str(fva_max_c))

      #get the maximum absolute values for drought and control
      max_abs_d = max(abs(fva_min_d),abs(fva_max_d))
      max_abs_c = max(abs(fva_min_c),abs(fva_max_c))

      #do math to make the comparison
      comparison = max_abs_d - max_abs_c

      #ensure comparison is significant in tolerance
      if(comparison >= 1E-7):

        #for debugging
        print("increased flux space magnitude in drought: ",rxn,"\tdrought max abs: ",max_abs_d,"\tcontrol max abs: ",max_abs_c)

        #determine if it is downregulated in the DGE analysis
        downregulated = False

        #next, check GPR, see if downregulated in the tissue where the change in flux is present
        match = re.search(r'__(\w)___(LIGHT|DARK)', rxn)

        try:

          tissue = match.group(1)

          #get set of associated genes
          genes = drought_model.reactions[drought_model.reactions.index(rxn)].genes

          #get reaction tissue

          #for each gene
          for gene in genes:

            print(gene.id)

            #from the tissue, search if that is downregulated in that tissue
            if tissue == "S":

              if gene.id in down_stem:

                print("gene "+gene.id+" is downregulated in the stem!")

                downregulated = True

              elif gene.id in up_stem:

                print("gene "+gene.id+" is upregulated in the stem!")

              else:

                print("gene "+gene.id+" is not siginficantly differently regulated in the stem")

            elif tissue == "R":

              if gene.id in down_root:

                print("gene "+gene.id+" is downregulated in the root!")

                downregulated = True

              elif gene.id in up_stem:

                print("gene "+gene.id+" is upregulated in the root!")

              else:

                print("gene "+gene.id+" is not siginficantly differently regulated in the root")

            elif tissue == "L":

              if gene.id in down_root:

                print("gene "+gene.id+" is downregulated in the leaf!")

                downregulated = True

              elif gene.id in up_stem:

                print("gene "+gene.id+" is upregulated in the leaf!")

              else:

                print("gene "+gene.id+" is not siginficantly differently regulated in the leaf")

          #if here then the reaction a cadidate
          if downregulated:

            kd_cand_f.write("\n\""+rxn+"\"")

        except:

          print("need to analyze ",rxn," manually!!!")

kd_cand_f.write("\n/")

kd_cand_f.close()

#copy the file into the gams folder
shutil.copyfile("./kd_results/kd_candidates_"+harvest+".txt","./GAMS/kd_candidates_"+harvest+".txt")


analyzing reaction  RXN_UDPREDUCT_RXN_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_E2C_mg2__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_ICOSANOYL_COA_SYNTHASE_RXN_er__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_GPH_RXN_er__L___LIGHT
min_d:  0.0 	max_d:  12.36993691 min_c:  0.0 	max_c:  18.18155443

analyzing reaction  RXN_RXN_15816__L___LIGHT
min_d:  0.0 	max_d:  128.60245305 min_c:  0.0 	max_c:  130.67464335

analyzing reaction  RXN_Trans_oxygen_molecule_m__L___LIGHT
min_d:  -4499.04670368 	max_d:  64.30122653 min_c:  -4499.50567833 	max_c:  65.33732167

analyzing reaction  RXN_Trans_cpd_12860_er__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_GLUTATHIONE_REDUCT_NADPH_RXN_c__L___LIGHT
min_d:  -64.30122653 	max_d:  0.0 min_c:  -65.33732167 	max_c:  0.0

analyzing reaction  RXN_RXN1F_155_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 

min_d:  -128.60245305 	max_d:  0.0 min_c:  -130.67464335 	max_c:  0.0

analyzing reaction  RXN_Trans_alpha_glucose_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_10704_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_cpd_12607_m__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_acp_c2p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXNQT_4394_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_10706_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_cpd1f_118_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_ATPASE_RXN_m__L___LIGHT
min_d:  0.0 	max_d:  349.45071772 min_c:  0.0 	max_c:  357.78701755

analyzing reaction  RXN_RIBULP3EPIM_RXN_p__L___LIGHT
min_d:  -92.24125164 	max_d:  -19.43901878 min_c

min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_indole_3_acetyl_leu_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_5282_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN0_5114_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_1_5_1_20_RXN_m__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_MALATE_DEHYDROGENASE_NADP_RXN_c__L___LIGHT
min_d:  -344.59096302 	max_d:  10000.0 min_c:  -355.20227552 	max_c:  10000.0

analyzing reaction  RXN_ALDOSE_1_EPIMERASE_RXN_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_UDPGLUCEPIM_RXN_m__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_GLUTAMATE_DEHYDROGENASE_NADP_RXN_m__L___LIGHT
min_d:  -116.48357257 	max_d:  9995.1402453 min_c:  -119.26233918 	max_c:  9997.41525796

analyzing reaction

min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_1103_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RIBULOKIN_RXN_er__L___LIGHT
min_d:  -349.45071772 	max_d:  0.0 min_c:  -357.78701755 	max_c:  0.0

analyzing reaction  RXN_Trans_fru1p_m__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_PEPDEPHOS_RXN_er__L___LIGHT
min_d:  -116.48357257 	max_d:  0.0 min_c:  -119.26233918 	max_c:  0.0

analyzing reaction  RXN_Trans_cpd6666_1_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_MG_PROTOPORPHYRIN_METHYLESTER_SYN_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_URIDINEKIN_RXN_g__L___LIGHT
min_d:  0.0 	max_d:  349.45071772 min_c:  0.0 	max_c:  357.78701755

analyzing reaction  RXN_LACTALDDEHYDROG_RXN_c__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN_10696_p__L___LIGHT


min_d:  0.0 	max_d:  64.30122652 min_c:  0.0 	max_c:  65.33732167

analyzing reaction  RXN_TRANS_CINNAMATE_4_MONOOXYGENASE_RXN_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_HOMOCYSMETB12_RXN_p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_R02437_c__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_1_6_5_4_RXN_c__L___LIGHT
min_d:  0.0 	max_d:  128.60245305 min_c:  0.0 	max_c:  130.67464335

analyzing reaction  RXN_2_4_1_123_RXN_g__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_gal_gal_xyl_proteins_g__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_palmityl_coa_c2p__L___LIGHT
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_ALANINE__GLYOXYLATE_AMINOTRANSFERASE_RXN_er__L___LIGHT
min_d:  0.0 	max_d:  12.36993691 min_c:  0.0 	max_c:  18.18155443

analyzing reaction

...

Potri.001G423700
gene Potri.001G423700 is not siginficantly differently regulated in the root
Potri.006G074500
gene Potri.006G074500 is not siginficantly differently regulated in the root
Potri.010G101900
gene Potri.010G101900 is not siginficantly differently regulated in the root
Potri.015G031300
gene Potri.015G031300 is not siginficantly differently regulated in the root
Potri.006G110900
gene Potri.006G110900 is not siginficantly differently regulated in the root
Potri.008G139300
gene Potri.008G139300 is not siginficantly differently regulated in the root
Potri.008G139100
gene Potri.008G139100 is not siginficantly differently regulated in the root
Potri.001G191000
gene Potri.001G191000 is downregulated in the root!

analyzing reaction  RXN_2_7_7_1_RXN_g__R___DARK
min_d:  0.0 	max_d:  7.756e-05 min_c:  0.0 	max_c:  1.17e-06
increased flux space magnitude in drought:  RXN_2_7_7_1_RXN_g__R___DARK 	drought max abs:  7.756e-05 	control max abs:  1.17e-06
Potri.005G032300
gene Potri.005G03

min_d:  1.562e-05 	max_d:  1.562e-05 min_c:  1.68e-05 	max_c:  1.68e-05

analyzing reaction  RXN_4_1_1_80_RXN_c__R___DARK
min_d:  0.00291037 	max_d:  0.00294332 min_c:  0.00316461 	max_c:  0.00316486

analyzing reaction  RXN_GMP_SYN_NH3_RXN_g__R___DARK
min_d:  0.0 	max_d:  3.154e-05 min_c:  1.553e-05 	max_c:  1.727e-05
increased flux space magnitude in drought:  RXN_GMP_SYN_NH3_RXN_g__R___DARK 	drought max abs:  3.154e-05 	control max abs:  1.727e-05
Potri.003G128200
gene Potri.003G128200 is upregulated in the root!

analyzing reaction  RXN_Trans_cpd_416_p__R___DARK
min_d:  0.00108872 	max_d:  0.00111761 min_c:  0.00120152 	max_c:  0.00120174

analyzing reaction  RXN_Trans_mevalonate_er__R___DARK
min_d:  -9.717e-05 	max_d:  0.0 min_c:  -7.1e-07 	max_c:  0.0
increased flux space magnitude in drought:  RXN_Trans_mevalonate_er__R___DARK 	drought max abs:  9.717e-05 	control max abs:  7.1e-07

analyzing reaction  RXN_Trans_2_lysophosphatidylcholines_er__R___DARK
min_d:  -1.759e-05 	max_d: 

min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_cpd_729_m__R___DARK
min_d:  -0.0 	max_d:  0.0 min_c:  -0.0 	max_c:  0.0

analyzing reaction  RXN_Trans_3_oxo_hexanoyl_acps_m__R___DARK
min_d:  -0.00192223 	max_d:  -0.00192223 min_c:  -0.00206691 	max_c:  -0.00206691

analyzing reaction  RXN_Trans_cpd_4578_er__R___DARK
min_d:  -0.00097786 	max_d:  -0.00094618 min_c:  -0.00101759 	max_c:  -0.00101739

analyzing reaction  RXN_Trans_cpd_4578_x__R___DARK
min_d:  0.00094618 	max_d:  0.00097786 min_c:  0.00101739 	max_c:  0.00101759

analyzing reaction  RXN_Trans_2_aceto_lactate_p__R___DARK
min_d:  0.00054344 	max_d:  0.00054344 min_c:  0.00058435 	max_c:  0.00058435

analyzing reaction  RXN_Trans_cpd_9965_p__R___DARK
min_d:  -0.00118189 	max_d:  -0.00118189 min_c:  -0.00127085 	max_c:  -0.00127085

analyzing reaction  RXN_Trans_2_aceto_lactate_m__R___DARK
min_d:  -0.00054344 	max_d:  -0.00054344 min_c:  -0.00058435 	max_c:  -0.00058435

analyzing reaction  RXN_

increased flux space magnitude in drought:  RXN_THIOREDOXIN_RXN_c__S___DARK 	drought max abs:  0.00012496 	control max abs:  1.01e-06

analyzing reaction  RXN_THIOREDOXIN_REDUCT_NADPH_RXN_c__L___DARK
min_d:  0.0 	max_d:  0.00019106 min_c:  0.0 	max_c:  1.54e-06
increased flux space magnitude in drought:  RXN_THIOREDOXIN_REDUCT_NADPH_RXN_c__L___DARK 	drought max abs:  0.00019106 	control max abs:  1.54e-06

analyzing reaction  RXN_THIOREDOXIN_REDUCT_NADPH_RXN_c__S___DARK
min_d:  0.0 	max_d:  0.00012496 min_c:  0.0 	max_c:  1.01e-06
increased flux space magnitude in drought:  RXN_THIOREDOXIN_REDUCT_NADPH_RXN_c__S___DARK 	drought max abs:  0.00012496 	control max abs:  1.01e-06

analyzing reaction  RXN_1_18_1_2_RXN_p__R___DARK
min_d:  -0.00603629 	max_d:  -0.0049369 min_c:  -0.00649063 	max_c:  -0.00648664

analyzing reaction  RXN_RXN1YI0_15_p__L___DARK
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	max_c:  0.0

analyzing reaction  RXN_RXN1YI0_15_p__S___DARK
min_d:  0.0 	max_d:  0.0 min_c:  0.0 	m

'./GAMS/kd_candidates_H2.txt'